In [2]:
from cura import github_ingestion
from cura import vector_store

print("Ingesting GitHub data, please input the following information:")
url = "MarkCodering/mindify-website"
access_token = input("GitHub Access Token: ")

print("Ingesting GitHub data...")
github_repo_data = github_ingestion.ingest_github_repo(url, access_token)

Ingesting GitHub data, please input the following information:
Ingesting GitHub data...
Ingesting files from the repository...


100%|██████████| 75/75 [00:43<00:00,  1.73it/s]


In [3]:
collection_name = url.replace("/", "_")
collection = vector_store.set_up_chromadb(collection_name)
ids = []
for i in range(len(github_repo_data[0])):
    ids.append(str(i))
    
print("Storing GitHub data in ChromaDB...")
collection.add(ids=ids, documents=github_repo_data[0])

Storing GitHub data in ChromaDB...


In [4]:
# Query the data from the vector store
print("Querying the data from the vector store...")
prompt = "What is Mindify AI?"
results = collection.query(
    query_texts=[prompt], # Chroma will embed this for you
    n_results=2 # how many results to return
)
print(results["documents"][0][0])

Querying the data from the vector store...
---
// @ts-ignore
const features = [
  {
    title: "Learn AI Technologies",
    description:
      "We provide online and in-person training to help you learn the latest generative AI technologies.",
  },
  {
    title: "Deploy AI Solutions",
    description:
      "We provide a platform for developers to deploy generative AI solutions in their projects.",
  },
  {
    title: "Fast Prototyping and Concept Validation",
    description:
      "We help you quickly prototype and validate your AI concepts to bring them to market faster.",
  },
];
---

<div class="mt-16 md:mt-0">
  <h2 class="text-4xl lg:text-5xl font-bold lg:tracking-tight text-center">
    About Mindify AI
  </h2>
  <p class="text-lg mt-4 text-slate-600">
    Mindify is an AI solution company that provides a platform for developers to
    learn and deploy generative AI solutions. We deliver online and in-person
    training to help you learn the latest AI technologies and deploy 

In [5]:
from cura import openai_chat

question = (
    "You are a smart and helpful AI programmer and here is the repository I am working on: {}".format(
        url
    )
    + "And, I wonder if you can help me with the following question with the following question: {}".format(
        prompt
    )
    + "based on the data in the repository which is available here: {}".format(
        results["documents"][0][0]
    )
)
print("Asking OpenAI the following question: {}".format(question))

answer = openai_chat.ask_question(question)

Asking OpenAI the following question: You are a smart and helpful AI programmer and here is the repository I am working on: MarkCodering/mindify-websiteAnd, I wonder if you can help me with the following question with the following question: What is Mindify AI?based on the data in the repository which is available here: ---
// @ts-ignore
const features = [
  {
    title: "Learn AI Technologies",
    description:
      "We provide online and in-person training to help you learn the latest generative AI technologies.",
  },
  {
    title: "Deploy AI Solutions",
    description:
      "We provide a platform for developers to deploy generative AI solutions in their projects.",
  },
  {
    title: "Fast Prototyping and Concept Validation",
    description:
      "We help you quickly prototype and validate your AI concepts to bring them to market faster.",
  },
];
---

<div class="mt-16 md:mt-0">
  <h2 class="text-4xl lg:text-5xl font-bold lg:tracking-tight text-center">
    About Mindify AI

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [6]:
print(answer.content)

Based on the provided data from the repository, Mindify AI is an AI solution company that focuses on providing a platform for developers to learn and deploy generative AI solutions. Here are the key aspects of Mindify AI:

1. **Learning AI Technologies**: Mindify AI offers both online and in-person training to help individuals and developers learn the latest generative AI technologies.

2. **Deploying AI Solutions**: The platform allows developers to deploy generative AI solutions in their projects, facilitating the integration of advanced AI capabilities.

3. **Fast Prototyping and Concept Validation**: Mindify AI assists in quickly prototyping and validating AI concepts, enabling faster time-to-market for AI-driven products and solutions.

The mission of Mindify AI is to help developers and businesses bring their AI concepts to market more quickly and deliver value to their customers through advanced AI technologies.

Here is a summary of the features provided by Mindify AI:
- **Lear

In [7]:
import gradio as gr

def echo(question):
    # Query the collection with the provided question
    results = collection.query(
        query_texts=[question],  # Chroma will embed this for you
        n_results=1  # Number of results to return
    )
    
    # Append the retrieved document to the question
    question = question + results["documents"][0][0]
    
    # Use OpenAI's chat to ask the modified question
    answer = openai_chat.ask_question(question)
    
    # Return the content of the answer
    return answer.content

# Define the Gradio interface
iface = gr.Interface(
    fn=echo,
    inputs=gr.Textbox(lines=2, placeholder="Enter your question here..."),
    outputs=gr.Code(label="Answer", language="markdown"),
)

# Launch the Gradio interface
iface.launch()


/Users/mark/Documents/Mindify/CURA-alpha/.venv/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.
